In [2]:
import numpy as np
import pandas as pd
pd.options.display.max_rows = 10
np.set_printoptions(precision=4, suppress=True)
import json

import glob, os
import re

import subprocess

In [3]:
pathfolder = ''
#example path:
#C:\\Users\\MSI\\Desktop\\Thesis\\NewDataSets\\rumoureval2019\\rumoureval-2019-training-data
#Paths may (and will) differ, but the destination should be "\\rumoureval2019\\rumoureval-2019-training-data"

annotation = pd.read_json('')
#example path:
#C:\\Users\\MSI\\Desktop\\Thesis\\NewDataSets\\rumoureval2019\\rumoureval-2019-training-data\\train-key.json
#Here, we need the "\\rumoureval2019\\rumoureval-2019-training-data\\train-key.json" to use as our annotation

devannotation = pd.read_json('')
#example path:
#C:\\Users\\MSI\\Desktop\\Thesis\\NewDataSets\\rumoureval2019\\rumoureval-2019-training-data\\dev-key.json
#The training dataset uses two keys as annotations, so we need the second one from "\\rumoureval2019\\rumoureval-2019-training-data\\dev-key.json"

export_destination = ''
#example path:
#'C:\\Users\\MSI\\Desktop\\Thesis\\Results\\test.tsv'
#Note: This can be anywhere, but the name must be "test.tsv"

trib_results = ''
#example path:
#'C:\\Users\\MSI\\Desktop\\Thesis\\Results\\phoeme\\Trib_results.csv'
#Note: This value takes the result of Tribrid_pos, so make sure that the name set on Tribrid_pos is the same as here

In [4]:
annotation = pd.concat([annotation,devannotation])

In [5]:
replyfoldername = "replies"

sourcefoldername = "source-tweet"

structurejsonname = "structure.json"

In [6]:
pos_support_label = 'support'
neg_support_label = 'deny'

# Data Preparation

In [7]:
def createtuplelist(structurepath):
    with open(structurepath) as f:
        lines = f.readlines()
    for i in lines:
        print(i,"\n")

    pattern = r'|\"|[[]]|:|[[]|[]]|\\|\''
    regex = re.compile(pattern, flags=re.IGNORECASE)

    lines2 = re.sub(pattern,'',str(lines))
    #print(lines2)

    splitlines = re.split('(\w*.)', lines2)
    splitlines = [i for i in splitlines if i and i != splitlines[0]]
    #print("\nsplitlines:",splitlines,"\n")

    sources =[]
    perspective = ""
    tupleset = []

    for i in range(len(splitlines)-1):
        if not i == 0:
            if i == 1:
                sources.append(splitlines[i][:len(splitlines[i]) -1])

            perspective = splitlines[i][:len(splitlines[i]) -1]
            tupleset.append([sources[-1], perspective])

            if splitlines[i].endswith("{"):
                sources.append(splitlines[i][:len(splitlines[i]) -1])
            if splitlines[i].endswith("}"):
                sources.pop()
            if not perspective:
                tupleset.pop()

    #for i in range(len(tupleset)):
            #print(i,tupleset[i][0],tupleset[i][1])
            
    return(tupleset)

In [8]:
def createtwittertuplelist(structurepath):
    with open(structurejson) as f:
        #print("4")
        lines = f.readlines()
    #for i in lines:
        #print(i,"\n")

    #convert the json with regex to only contain '{' ',' numbers and '}'    
    pattern = r'|\"|[[]]|:|[[]|[]]|\\|\''
    regex = re.compile(pattern, flags=re.IGNORECASE)

    lines2 = re.sub(pattern,'',str(lines))

    #split them by numbers and non-numbers to create a tupleset of the interactions
    splitlines = re.split('(\d*.)', lines2)
    splitlines = [i for i in splitlines if i and i != splitlines[0]]

    sources =[]
    perspective = ""
    tupleset = []

    #the split string are turned into tuple-sets as follows : first number is the claim, 
    #the second is perspective the first set of tuples is always the same
    #number on both sides, to indicate that it's a new thread
#

#
    for i in range(len(splitlines)):
        #print("6")
        if not i == 0:
            #print("7")
            if i == 1:
                #print("8")
                sources.append(splitlines[i][:len(splitlines[i]) -1])
                #print("9")

            perspective = splitlines[i][:len(splitlines[i]) -1]
            tupleset.append([sources[-1], perspective])
            #print("10")

            if splitlines[i].endswith("{"):
                sources.append(splitlines[i][:len(splitlines[i]) -1])
                #print("11")
            if splitlines[i].endswith("}"):
                sources.pop()
                #print("12")
            if not perspective:
                tupleset.pop()
                #print("13")
    return(tupleset)

In [9]:
%%time
# copy of copy to put print between every line
# <<<<<<<RUN THIS

df =pd.DataFrame(
{"Label" : [], 
"x" : [], 
"y" : [],
"claim" : [], 
"perspective" : []})


label = ""
reply = ""
source = ""
unimportantcount = 0
unimportantmarks=[]

newsbookmarks=[0]
threadbookmarks = [0]
pnumber = 0
alltuples = []

#print("0:",pathfolder)
#print("0")
for trainfolders in os.listdir(pathfolder):
    trainfolder = os.path.join(pathfolder, trainfolders) #\threads\en\all the folders
    #print("1")
    #print("1:",trainfolder)
    rightannotation = annotation
    if "reddit" in trainfolder:
        if os.path.isdir(trainfolder):
            #print("2")
            for topicfolders in os.listdir(trainfolder): 
                allreplies = os.path.join(trainfolder, topicfolders) #\threads\en\all the folders\ threads in number-form
                #print(allreplies)
                #print(allreplies)
                repliesfolder = os.path.join(allreplies, replyfoldername) #\threads in number-form\reactions
                sourcefolder = os.path.join(allreplies, sourcefoldername)
                structurejson = os.path.join(allreplies, structurejsonname)
                #print("3")
    #######            
    ####        
                #print(structurejson)
                tupleset = createtuplelist(structurejson)
                alltuples.append(tupleset) # save all tuplesets to access later for grading

                for i in range(len(tupleset)):
                    #print("14")
                    #print(tupleset,tupleset[i])
                    #############################################
                    if tupleset[i][0] == tupleset[i][1]: # claim = TOPIC, perspective = THREAD
                        #print("14.1")
                        for sources in os.listdir(sourcefolder):
                            #print("14.2")
                            sourcepath = os.path.join(sourcefolder, sources)
                            sourcejson = pd.read_json(sourcepath) 
                            #print("14.3")
                        presource = sourcejson.loc['children','data']
                        normedf = pd.json_normalize(presource)
                        #print("hsh")
                        ####source = os.path.basename(os.path.normpath(trainfolder))
                        #print("14/s")
                        reply = normedf.iloc[0]['data.title']
                        source = reply
                        #print("14/6")
                        #determine label
                        print("annloc:",annotation.loc[tupleset[i][0]]['subtaskaenglish'])
                        if annotation.loc[tupleset[i][0]]['subtaskaenglish'] == pos_support_label: 
                            print("true!")
                            label = "1"
                        elif annotation.loc[tupleset[i][0]]['subtaskaenglish'] == neg_support_label: 
                            print("false!")
                            label = "0"
                        else:
                            print("ireelevant!")
                            label = "0"
                            unimportantmarks.append(len(df.index))



                    else: #claim = THREAD, perspective = TWEET   
                        #print("20")
                        for sources in os.listdir(sourcefolder):
                            sourcepath = os.path.join(sourcefolder, sources)
                            sourcejson = pd.read_json(sourcepath)

                            #print("21")
                        #check if claim in sourcefolder    
                        if tupleset[i][0] in str(sourcejson):
                            #print("[0] in sourcejson", sources)
                            #print("22")
                            presource = sourcejson.loc['children','data']
                            sourcedf = pd.json_normalize(presource)
                            source = sourcedf.iloc[0]['data.title'] #claim


                        #check if claim in repliesfolder
                        else:
                            #print("23")
                            magicnum = str(tupleset[i][0])
                            magicnum +=".json"
                            #print(magicnum)
                            replypath = replypath = os.path.join(repliesfolder,magicnum)                        
                            if os.path.isfile(replypath):
                                #print(replypath,"is correct!")
                                replyjson = pd.read_json(replypath)
                                source = replyjson.loc['body','data']
                            #print("24 but better")


                        #get perspective from the sourcefolder            
                        if tupleset[i][1] in str(sourcejson):
                            #print("26")
                            label = "0"
                            #print("[1] in sourcejson")
                            presource = sourcejson.loc['children','data']
                            sourcedf = pd.json_normalize(presource)
                            source = sourcedf.iloc[0]['data.title'] #claim
                            # get label
                            sourcenumber = tupleset[i][0]
                            if sourcesnumber in annotation.index:
                                #print("27")
                                stance = annotation.loc[sourcesnumber,"subtaskaenglish"]   
                            print("stance",stance)
                            if stance == pos_support_label:
                                #print("28")
                                label = "1"
                            elif stance == neg_support_label:
                                #print("29")
                                label = "0" #label 
                        #get perspective from the repliesfolder
                        else:
                            #print("30")
                            label = "0"

                            magicnum = str(tupleset[i][1])
                            magicnum +=".json"
                            #print(magicnum)
                            replypath = replypath = os.path.join(repliesfolder,magicnum)                        
                            if os.path.isfile(replypath):
                                #print(replypath,"is correct!")
                                replyjson = pd.read_json(replypath)
                                try: 
                                    reply = replyjson.loc['body','data']
                                    #print("reply had body")
                                except:
                                    reply = "0"
                                    unimportantcount += 1
                                    unimportantmarks.append(len(df.index))
                                    #print("reply didnt have body")
                            #print("31 but better")

                            pnumber = tupleset[i][1]
                            if pnumber in annotation.index:
                                #print("32")
                                print("finalstance",annotation.loc[pnumber, 'subtaskaenglish'])
                                if not pd.isnull(annotation.loc[pnumber, 'subtaskaenglish']):
                                    #print("33")
                                    stance =  annotation.loc[pnumber,"subtaskaenglish"]
                                if stance == pos_support_label:
                                    #print("36")
                                    label = "1"
                                elif stance == neg_support_label:
                                    #print("37")
                                    label = "0"
                                else:
                                    #print("38")
                                    label = "0"
                                    unimportantcount +=1
                                    unimportantmarks.append(len(df.index))

                    #print(label, "0", "0", source, "||",reply)
                    df.loc[len(df.index)] = [label, "0", "0", source, reply] ### label=0 for now, bc we don't need it
                    print(df.loc[len(df.index)-1])
                    #print("39")
                    print("<<<<<<<",len(df.index), len(tupleset))
                threadbookmarks.append(len(df.index)-1)
        newsbookmarks.append(len(df.index))

##################################################
###################################################
##################################################

#get the same twitter code from PHEME-code        
    elif "twitter" in trainfolder:
        #print("wop")
        #print(trainfolder)
        if os.path.isdir(trainfolder):
            #print("2")
            for newtrainfolders in os.listdir(trainfolder):
                newtrainfolder = os.path.join(trainfolder,newtrainfolders)
                for topicfolders in os.listdir(newtrainfolder): 
                    allreplies = os.path.join(newtrainfolder, topicfolders) #\threads\en\all the folders\ threads in number-form
                    #print(allreplies)
                    #print(allreplies)
                    repliesfolder = os.path.join(allreplies, replyfoldername) #\threads in number-form\reactions
                    sourcefolder = os.path.join(allreplies, sourcefoldername)
                    structurejson = os.path.join(allreplies, structurejsonname)
                    #print("3")
        #######     
                    #open the tweet structure json
                    tupleset = createtwittertuplelist(structurejson)
                    alltuples.append(tupleset) # save all tuplesets to access later for grading

                    for i in range(len(tupleset)):
                        #print("14")
                        #print(tupleset,tupleset[i])
                        #############################################
                        if tupleset[i][0] == tupleset[i][1]: # claim = TOPIC, perspective = THREAD
                            #print("14.1")
                            for sources in os.listdir(sourcefolder):
                                #print("14.2")
                                sourcepath = os.path.join(sourcefolder, sources)
                                sourcejson = pd.read_json(sourcepath) 
                                #print("14.3")
                            reply = sourcejson.loc['symbols','text']
                            source = os.path.basename(os.path.normpath(trainfolder))
                            #print("14/6")
                            #determine label
                            print("twitanno:",annotation.loc[tupleset[i][0]]['subtaskaenglish'])
                            if annotation.loc[tupleset[i][0]]['subtaskaenglish'] == pos_support_label: 
                                print("tr")
                                label = "1"
                            elif annotation.loc[tupleset[i][0]]['subtaskaenglish'] == neg_support_label: 
                                print("fal")
                                label = "0"
                            else:
                                print("irr")
                                label = "0"
                                unimportantmarks.append(len(df.index))
                            #print("14/3")

                        #############################################
                        else: #claim = THREAD (source-tweet), perspective = TWEET(replies)   
                            #print("20")
                            for sources in os.listdir(sourcefolder):
                                sourcepath = os.path.join(sourcefolder, sources)
                                sourcejson = pd.read_json(sourcepath)
                                #print("21")
                            #check if claim in sourcefolder    
                            if tupleset[i][0] in str(sourcejson):
                                #print("[0] in sourcejson", sources)
                                #print("22")
                                source = sourcejson.loc['symbols','text'] #claim

                            #check if claim in repliesfolder
                            else:
                                #print("23")
                                magicnum = str(tupleset[i][0])
                                magicnum +=".json"
                                #print(magicnum)
                                replypath = replypath = os.path.join(repliesfolder,magicnum)                        
                                if os.path.isfile(replypath):
                                    #print(replypath,"is correct!")
                                    replyjson = pd.read_json(replypath)
                                    source = replyjson.loc['symbols','text']
                                #print("24 but better")


                            #get perspective from the sourcefolder            
                            if tupleset[i][1] in str(sourcejson):
                                #print("26")
                                label = "0"
                                #print("[1] in sourcejson")
                                source = sourcejson.loc['symbols','text'] #claim
                                # get label
                                sourcenumber = tupleset[i][0]
                                if sourcesnumber in annotationkey.index:
                                    #print("27")
                                    stance = annotationkey.loc[sourcesnumber,"support"]   
                                    print("twitstance",stance)
                                if stance == "supporting":
                                    #print("28")
                                    label = "1"
                                elif stance == "denying":
                                    #print("29")
                                    label = "0" #label 
                            #get perspective from the repliesfolder
                            else:
                               # print("30")
                                label = "0"

                                magicnum = str(tupleset[i][1])
                                magicnum +=".json"
                                #print(magicnum)
                                replypath = replypath = os.path.join(repliesfolder,magicnum)                        
                                if os.path.isfile(replypath):
                                    #print(replypath,"is correct!")
                                    replyjson = pd.read_json(replypath)
                                    reply = replyjson.loc['symbols','text']
                                #print("31 but better")

                                pnumber = int(tupleset[i][1])
                                if pnumber in annotation.index:
                                    #print("32")
                                    print("tweetfinalstance",annotation.loc[pnumber, 'subtaskaenglish'])
                                    if not pd.isnull(annotation.loc[pnumber, 'subtaskaenglish']):
                                        #print("33")
                                        stance =  annotation.loc[pnumber,"subtaskaenglish"]
                                    if stance == pos_support_label:
                                        #print("36")
                                        label = "1"
                                    elif stance == neg_support_label:
                                        #print("37")
                                        label = "0"
                                    else:
                                        #print("38")
                                        label = "0"
                                        unimportantcount +=1
                                        unimportantmarks.append(len(df.index))

                        #print(label, "0", "0", source, "||",reply)
                        df.loc[len(df.index)] = [label, "0", "0", source, reply] ### label=0 for now, bc we don't need it
                        print(df.loc[len(df.index)-1])
                        #print("39")
                        print("<<<<<<<",len(df.index), len(tupleset))
                    threadbookmarks.append(len(df.index)-1)
            newsbookmarks.append(len(df.index))

{"1jvbd8":{"cbiol38":{"cbiwlli":[]},"cbj4pcw":[],"cbkixew":[]}}
 

annloc: deny
false!
Label                                                          0
x                                                              0
y                                                              0
claim          Fukushima spewing equivalent of 112 Hiroshima-...
perspective    Fukushima spewing equivalent of 112 Hiroshima-...
Name: 0, dtype: object
<<<<<<< 1 5
finalstance comment
Label                                                          0
x                                                              0
y                                                              0
claim          Fukushima spewing equivalent of 112 Hiroshima-...
perspective    The bombs dropped during world war 2 were fair...
Name: 1, dtype: object
<<<<<<< 2 5
finalstance comment
Label                                                          0
x                                                              0
y                      

<ipython-input-7-3f343e673184>:8: FutureWarning: Possible nested set at position 5
  regex = re.compile(pattern, flags=re.IGNORECASE)
<ipython-input-7-3f343e673184>:8: FutureWarning: Possible nested set at position 12
  regex = re.compile(pattern, flags=re.IGNORECASE)
<ipython-input-7-3f343e673184>:10: FutureWarning: Possible nested set at position 5
  lines2 = re.sub(pattern,'',str(lines))
<ipython-input-7-3f343e673184>:10: FutureWarning: Possible nested set at position 12
  lines2 = re.sub(pattern,'',str(lines))


finalstance comment
Label                                                          0
x                                                              0
y                                                              0
claim                   Please don't give Thunderf00t any views.
perspective    Devil's advocate here: why? I've watched some ...
Name: 8, dtype: object
<<<<<<< 9 19
finalstance comment
Label                                                          0
x                                                              0
y                                                              0
claim          Devil's advocate here: why? I've watched some ...
perspective    I'd say more likely, his videos on topics that...
Name: 9, dtype: object
<<<<<<< 10 19
finalstance support
Label                                                          1
x                                                              0
y                                                              0
claim          I'd say

<<<<<<< 36 13
finalstance comment
Label                                                          0
x                                                              0
y                                                              0
claim          Its easiest to debunk by reading the actual ar...
perspective    One thing "scare articles" seldom mention is t...
Name: 36, dtype: object
<<<<<<< 37 13
{"5qzxep":{"dd3e2ma":[],"dd3dvp6":[],"dd3dx94":[],"dd3e1x7":[]}}
 

annloc: query
ireelevant!
Label                                                          0
x                                                              0
y                                                              0
claim          Is it true that if you have your phone on char...
perspective    Is it true that if you have your phone on char...
Name: 37, dtype: object
<<<<<<< 38 5
finalstance comment
Label                                                          0
x                                                             

finalstance comment
Label                                    0
x                                        0
y                                        0
claim          My brother is a moron then.
perspective                My condolences.
Name: 62, dtype: object
<<<<<<< 63 19
finalstance comment
Label                        0
x                            0
y                            0
claim          My condolences.
perspective          Thanks :(
Name: 63, dtype: object
<<<<<<< 64 19
finalstance deny
Label                                                          0
x                                                              0
y                                                              0
claim                                            My condolences.
perspective    It's not. Many pro athletes believe it, but th...
Name: 64, dtype: object
<<<<<<< 65 19
finalstance comment
Label                                                          0
x                                                

...

Label                                                          0
x                                                              0
y                                                              0
claim          UPDATE: Hostages fleeing #Sydney cafe held by ...
perspective                  @FoxNews any update on PA shooting?
Name: 6944, dtype: object
<<<<<<< 6945 15
Label                                                          0
x                                                              0
y                                                              0
claim          UPDATE: Hostages fleeing #Sydney cafe held by ...
perspective    @FoxNews  Was he saying "hands up don't shoot"...
Name: 6945, dtype: object
<<<<<<< 6946 15
Label                                                          0
x                                                              0
y                                                              0
claim          UPDATE: Hostages fleeing #Sydney cafe held by ...
perspe

Label                                                          0
x                                                              0
y                                                              0
claim          #SydneySiege: Latest video of hostages escapin...
perspective    @FoxNews @AmericaNewsroom Illegal Aliens will ...
Name: 6970, dtype: object
<<<<<<< 6971 16
Label                                                          0
x                                                              0
y                                                              0
claim          #SydneySiege: Latest video of hostages escapin...
perspective    @FoxNews How long before Fox viewers blame thi...
Name: 6971, dtype: object
<<<<<<< 6972 16
Label                                                          0
x                                                              0
y                                                              0
claim          #SydneySiege: Latest video of hostages escapin...
perspe

Label                                                          1
x                                                              0
y                                                              0
claim                                            twitter-english
perspective    #BREAKING: Police have confirmed that the #Syd...
Name: 6994, dtype: object
<<<<<<< 6995 17
Label                                                          0
x                                                              0
y                                                              0
claim          #BREAKING: Police have confirmed that the #Syd...
perspective    “@9NewsSyd: #BREAKING: Police have confirmed t...
Name: 6995, dtype: object
<<<<<<< 6996 17
Label                                                          0
x                                                              0
y                                                              0
claim          #BREAKING: Police have confirmed that the #Syd...
perspe

Label                                                          0
x                                                              0
y                                                              0
claim          #BREAKING: At least two people have died follo...
perspective                         @AusNewsNetwork noooooo :(((
Name: 7019, dtype: object
<<<<<<< 7020 17
Label                                                          0
x                                                              0
y                                                              0
claim          #BREAKING: At least two people have died follo...
perspective          @AusNewsNetwork what's happened to the guy!
Name: 7020, dtype: object
<<<<<<< 7021 17
Label                                                          0
x                                                              0
y                                                              0
claim          #BREAKING: At least two people have died follo...
perspe

Label                                                          0
x                                                              0
y                                                              0
claim          @emaccaz_ @Angus_OL I DIDNT WATCH THE VIDEO I ...
perspective    @vanilIapayne @Angus_OL people escaping and it...
Name: 7043, dtype: object
<<<<<<< 7044 19
Label                                                          0
x                                                              0
y                                                              0
claim          @Angus_OL @vanilIapayne THATS THE LADY FROM TH...
perspective                           @emaccaz_ omfg it is 😱😱😱😱😱
Name: 7044, dtype: object
<<<<<<< 7045 19
Label                                                          0
x                                                              0
y                                                              0
claim          Police confirm that #sydneysiege is finally ov...
perspe

In [10]:
df

Label  x  y                                              claim  \
0        0  0  0  Fukushima spewing equivalent of 112 Hiroshima-...   
1        0  0  0  Fukushima spewing equivalent of 112 Hiroshima-...   
2        0  0  0  The bombs dropped during world war 2 were fair...   
3        0  0  0  The bombs dropped during world war 2 were fair...   
4        0  0  0  The bombs dropped during world war 2 were fair...   
...    ... .. ..                                                ...   
7045     0  0  0  Police confirm that #sydneysiege is finally ov...   
7046     0  0  0  Police confirm that #sydneysiege is finally ov...   
7047     0  0  0  Police confirm that #sydneysiege is finally ov...   
7048     0  0  0  Police confirm that #sydneysiege is finally ov...   
7049     0  0  0  Police confirm that #sydneysiege is finally ov...   

                                            perspective  
0     Fukushima spewing equivalent of 112 Hiroshima-...  
1     The bombs dropped during world war 2 were fair...  
2     If I read this correctly, they only compared o...  
3     The iodine has an 8 day halflife the caesium 3...  
4     \nFukushima is still in the clean-up process. ...  
...                                                 ...  
7045                              @Angus_OL @horanosaur  
7046  @Angus_OL The 6 of us are watching this unfold...  
7047  @Angus_OL thank god they're all safe now. some...  
7048  @Angus_OL thank god its over, they're finally ...  
7049                                       @Angus_OL :(  

[7050 rows x 5 columns]

In [11]:
# regex: if '@' or 'htttp://', then delete whole string/ until theres a blank space
pattern = r'@|#|http(\S)*'
regex = re.compile(pattern, flags=re.IGNORECASE)

for i in range((len(df))):
    if (type(df['perspective'][i]) != float):
        df['perspective'][i] = regex.sub('', df['perspective'][i])
    if (type(df['claim'][i]) != float):
        df['claim'][i] = regex.sub('', df['claim'][i])

In [12]:
df

Label  x  y                                              claim  \
0        0  0  0  Fukushima spewing equivalent of 112 Hiroshima-...   
1        0  0  0  Fukushima spewing equivalent of 112 Hiroshima-...   
2        0  0  0  The bombs dropped during world war 2 were fair...   
3        0  0  0  The bombs dropped during world war 2 were fair...   
4        0  0  0  The bombs dropped during world war 2 were fair...   
...    ... .. ..                                                ...   
7045     0  0  0  Police confirm that sydneysiege is finally ove...   
7046     0  0  0  Police confirm that sydneysiege is finally ove...   
7047     0  0  0  Police confirm that sydneysiege is finally ove...   
7048     0  0  0  Police confirm that sydneysiege is finally ove...   
7049     0  0  0  Police confirm that sydneysiege is finally ove...   

                                            perspective  
0     Fukushima spewing equivalent of 112 Hiroshima-...  
1     The bombs dropped during world war 2 were fair...  
2     If I read this correctly, they only compared o...  
3     The iodine has an 8 day halflife the caesium 3...  
4     \nFukushima is still in the clean-up process. ...  
...                                                 ...  
7045                                Angus_OL horanosaur  
7046  Angus_OL The 6 of us are watching this unfold,...  
7047  Angus_OL thank god they're all safe now. some ...  
7048  Angus_OL thank god its over, they're finally s...  
7049                                        Angus_OL :(  

[7050 rows x 5 columns]

In [13]:
df = df.reset_index(drop=True)
df

Label  x  y                                              claim  \
0        0  0  0  Fukushima spewing equivalent of 112 Hiroshima-...   
1        0  0  0  Fukushima spewing equivalent of 112 Hiroshima-...   
2        0  0  0  The bombs dropped during world war 2 were fair...   
3        0  0  0  The bombs dropped during world war 2 were fair...   
4        0  0  0  The bombs dropped during world war 2 were fair...   
...    ... .. ..                                                ...   
7045     0  0  0  Police confirm that sydneysiege is finally ove...   
7046     0  0  0  Police confirm that sydneysiege is finally ove...   
7047     0  0  0  Police confirm that sydneysiege is finally ove...   
7048     0  0  0  Police confirm that sydneysiege is finally ove...   
7049     0  0  0  Police confirm that sydneysiege is finally ove...   

                                            perspective  
0     Fukushima spewing equivalent of 112 Hiroshima-...  
1     The bombs dropped during world war 2 were fair...  
2     If I read this correctly, they only compared o...  
3     The iodine has an 8 day halflife the caesium 3...  
4     \nFukushima is still in the clean-up process. ...  
...                                                 ...  
7045                                Angus_OL horanosaur  
7046  Angus_OL The 6 of us are watching this unfold,...  
7047  Angus_OL thank god they're all safe now. some ...  
7048  Angus_OL thank god its over, they're finally s...  
7049                                        Angus_OL :(  

[7050 rows x 5 columns]

In [14]:
print(len(threadbookmarks))

366


In [15]:
#print(unimportantmarks)
print(len(unimportantmarks))

1096


In [35]:
#export to csv/tsv
df.to_csv(export_destination, sep = '\t', index = False)

In [16]:
unimportantcount

1057

# Tribrid_pos for stance classificaiton

In [17]:
tribrid_results = pd.read_csv(trib_results)

In [18]:
tribrid_results

undermine_score  support_score  predict_label  gold
0           -6.432536       4.612656              1     0
1           -5.760370       3.770271              1     0
2           -4.887443       3.346289              1     0
3           -5.672469       4.138422              1     0
4            0.889168      -2.216456              0     0
...               ...            ...            ...   ...
7045         3.187705      -1.756415              0     0
7046         0.525223       1.250964              1     0
7047        -4.801109       7.499414              1     0
7048        -2.475894       4.763199              1     0
7049         1.485800       0.130995              0     0

[7050 rows x 4 columns]

In [19]:
#change the 0's to -1's to better calculate
for i in range(len(tribrid_results)):
    if tribrid_results['predict_label'][i] == 0:
        tribrid_results.at[i,'predict_label'] = -1
    if tribrid_results['gold'][i] == 0:
        tribrid_results.at[i,'gold'] = -1
        
    # if the row is unimportant, then mark it as 0
    #if i in unimportantmarks:
        #tribrid_results.at[i,'gold'] = 0

In [20]:
tribrid_results

undermine_score  support_score  predict_label  gold
0           -6.432536       4.612656              1    -1
1           -5.760370       3.770271              1    -1
2           -4.887443       3.346289              1    -1
3           -5.672469       4.138422              1    -1
4            0.889168      -2.216456             -1    -1
...               ...            ...            ...   ...
7045         3.187705      -1.756415             -1    -1
7046         0.525223       1.250964              1    -1
7047        -4.801109       7.499414              1    -1
7048        -2.475894       4.763199              1    -1
7049         1.485800       0.130995             -1    -1

[7050 rows x 4 columns]

In [21]:
threadbookmarks2 = []
[threadbookmarks2.append(x) for x in threadbookmarks if x not in threadbookmarks2]
#print(threadbookmarks2)
#print(len(threadbookmarks2))

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [22]:
flattuples = []
for i in range(len(alltuples)): #Traversing through the main list
  for j in range (len(alltuples[i])): #Traversing through each sublist
    flattuples.append(alltuples[i][j]) #Appending elements into our flat_list

newdf3 = tribrid_results.copy()
newdf3.rename(columns = {'undermine_score' : 'claim', 'support_score' : 'perspective', 'gold' : 'result'}, inplace = True)
newdf3 = newdf3.astype({"claim": str, "perspective": str})
for i in range(len(newdf3)):
    newdf3.at[i,'claim'] = flattuples[i][0][-5:]
    newdf3.at[i,'perspective'] = flattuples[i][1][-5:]
    #changing all values to thread/replynumbers

    if newdf3.at[i,'claim'] == newdf3.at[i,'perspective']:
        newdf3.at[i,'predict_label'] = newdf3.at[i,'result']
    #changing all thread "predictions" with results, as it is our guide to calculate how right/wrong people are
    
    else:
        claim_result = newdf3.index[newdf3['perspective'] == newdf3.at[i,'claim']]
        #find the claim's stance by getting the index(es)(but then getting the first instance of the index) 
        #of the claim's number in perspective column
        newdf3.at[i,'result'] = newdf3.at[claim_result[0],'result'] * newdf3.at[i,'predict_label']
    #changing the result with previous stance * this stance (written better in evernote)
print("len of df3:", len(newdf3))    
for i in range(len(newdf3)):
    print(newdf3.iloc[i],"\n")
#newdf3

len of df3: 7050
claim            jvbd8
perspective      jvbd8
predict_label       -1
result              -1
Name: 0, dtype: object 

claim            jvbd8
perspective      iol38
predict_label        1
result              -1
Name: 1, dtype: object 

claim            iol38
perspective      iwlli
predict_label        1
result              -1
Name: 2, dtype: object 

claim            jvbd8
perspective      j4pcw
predict_label        1
result              -1
Name: 3, dtype: object 

claim            jvbd8
perspective      kixew
predict_label       -1
result               1
Name: 4, dtype: object 

claim            1xv6u
perspective      1xv6u
predict_label        1
result               1
Name: 5, dtype: object 

claim            1xv6u
perspective      64vk3
predict_label       -1
result              -1
Name: 6, dtype: object 

claim            64vk3
perspective      9capm
predict_label       -1
result               1
Name: 7, dtype: object 

claim            9capm
perspective      9mbsa
p

claim            y3ajz
perspective      y3yea
predict_label        1
result               1
Name: 291, dtype: object 

claim            y3yea
perspective      y4btz
predict_label        1
result               1
Name: 292, dtype: object 

claim            y4btz
perspective      y4mn1
predict_label       -1
result              -1
Name: 293, dtype: object 

claim            y4mn1
perspective      ynx8e
predict_label       -1
result               1
Name: 294, dtype: object 

claim            ynx8e
perspective      1psjs
predict_label        1
result               1
Name: 295, dtype: object 

claim            1psjs
perspective      1qfqu
predict_label        1
result               1
Name: 296, dtype: object 

claim            1qfqu
perspective      1sc2m
predict_label        1
result               1
Name: 297, dtype: object 

claim            1qfqu
perspective      4meew
predict_label        1
result               1
Name: 298, dtype: object 

claim            y3yea
perspective      y4d0r
pr

Name: 564, dtype: object 

claim            6uw4y
perspective      8364h
predict_label        1
result              -1
Name: 565, dtype: object 

claim            8364h
perspective      83b4n
predict_label        1
result              -1
Name: 566, dtype: object 

claim            83b4n
perspective      83d42
predict_label        1
result              -1
Name: 567, dtype: object 

claim            83d42
perspective      83hb1
predict_label       -1
result               1
Name: 568, dtype: object 

claim            83hb1
perspective      83o2r
predict_label        1
result               1
Name: 569, dtype: object 

claim            83o2r
perspective      84h6u
predict_label        1
result               1
Name: 570, dtype: object 

claim            84h6u
perspective      85uol
predict_label        1
result               1
Name: 571, dtype: object 

claim            85uol
perspective      86kip
predict_label        1
result               1
Name: 572, dtype: object 

claim            86ki

Name: 807, dtype: object 

claim            5ba50
perspective      5gfmb
predict_label       -1
result              -1
Name: 808, dtype: object 

claim            938df
perspective      5b5rd
predict_label       -1
result               1
Name: 809, dtype: object 

claim            5b5rd
perspective      5gg51
predict_label        1
result               1
Name: 810, dtype: object 

claim            938df
perspective      5b76n
predict_label       -1
result               1
Name: 811, dtype: object 

claim            5b76n
perspective      5gk6d
predict_label        1
result               1
Name: 812, dtype: object 

claim            938df
perspective      5cumj
predict_label        1
result              -1
Name: 813, dtype: object 

claim            5cumj
perspective      5d2io
predict_label        1
result              -1
Name: 814, dtype: object 

claim            5d2io
perspective      5gewp
predict_label       -1
result               1
Name: 815, dtype: object 

claim            l23a

Name: 1078, dtype: object 

claim            u9bv5
perspective      0e1ul
predict_label       -1
result              -1
Name: 1079, dtype: object 

claim            0e1ul
perspective      4n4q3
predict_label       -1
result               1
Name: 1080, dtype: object 

claim            n9173
perspective      uqe3o
predict_label        1
result              -1
Name: 1081, dtype: object 

claim            n9173
perspective      ut9sw
predict_label        1
result              -1
Name: 1082, dtype: object 

claim            n9173
perspective      v7pl1
predict_label        1
result              -1
Name: 1083, dtype: object 

claim            unvgg
perspective      unvgg
predict_label       -1
result              -1
Name: 1084, dtype: object 

claim            unvgg
perspective      grhjw
predict_label       -1
result               1
Name: 1085, dtype: object 

claim            unvgg
perspective      grii0
predict_label       -1
result               1
Name: 1086, dtype: object 

claim       

...

claim            54880
perspective      61056
predict_label        1
result               1
Name: 5916, dtype: object 

claim            37184
perspective      61858
predict_label       -1
result              -1
Name: 5917, dtype: object 

claim            37184
perspective      79840
predict_label        1
result               1
Name: 5918, dtype: object 

claim            37184
perspective      33600
predict_label        1
result               1
Name: 5919, dtype: object 

claim            37184
perspective      55904
predict_label        1
result               1
Name: 5920, dtype: object 

claim            55904
perspective      19104
predict_label       -1
result              -1
Name: 5921, dtype: object 

claim            19104
perspective      76480
predict_label       -1
result              -1
Name: 5922, dtype: object 

claim            76480
perspective      56864
predict_label        1
result               1
Name: 5923, dtype: object 

claim            55904
perspective      

Name: 6177, dtype: object 

claim            91520
perspective      46592
predict_label        1
result               1
Name: 6178, dtype: object 

claim            91520
perspective      56192
predict_label       -1
result              -1
Name: 6179, dtype: object 

claim            56192
perspective      84512
predict_label        1
result               1
Name: 6180, dtype: object 

claim            91520
perspective      89186
predict_label       -1
result              -1
Name: 6181, dtype: object 

claim            91520
perspective      13088
predict_label        1
result               1
Name: 6182, dtype: object 

claim            91520
perspective      18944
predict_label        1
result               1
Name: 6183, dtype: object 

claim            91520
perspective      24288
predict_label        1
result               1
Name: 6184, dtype: object 

claim            24288
perspective      01216
predict_label       -1
result              -1
Name: 6185, dtype: object 

claim       

Name: 6459, dtype: object 

claim            52801
perspective      59360
predict_label       -1
result               1
Name: 6460, dtype: object 

claim            52801
perspective      96961
predict_label        1
result              -1
Name: 6461, dtype: object 

claim            52801
perspective      74400
predict_label        1
result              -1
Name: 6462, dtype: object 

claim            49121
perspective      54241
predict_label       -1
result              -1
Name: 6463, dtype: object 

claim            54241
perspective      10273
predict_label        1
result              -1
Name: 6464, dtype: object 

claim            49121
perspective      54464
predict_label        1
result               1
Name: 6465, dtype: object 

claim            49121
perspective      75488
predict_label        1
result               1
Name: 6466, dtype: object 

claim            75488
perspective      37953
predict_label        1
result               1
Name: 6467, dtype: object 

claim       

Name: 6737, dtype: object 

claim            89024
perspective      36864
predict_label       -1
result               1
Name: 6738, dtype: object 

claim            89024
perspective      08544
predict_label        1
result              -1
Name: 6739, dtype: object 

claim            08544
perspective      77888
predict_label        1
result               1
Name: 6740, dtype: object 

claim            89024
perspective      27904
predict_label        1
result              -1
Name: 6741, dtype: object 

claim            27904
perspective      27362
predict_label        1
result              -1
Name: 6742, dtype: object 

claim            89024
perspective      21856
predict_label        1
result              -1
Name: 6743, dtype: object 

claim            21856
perspective      07104
predict_label        1
result              -1
Name: 6744, dtype: object 

claim            89024
perspective      68384
predict_label       -1
result               1
Name: 6745, dtype: object 

claim       

Name: 7008, dtype: object 

claim            23552
perspective      49472
predict_label        1
result               1
Name: 7009, dtype: object 

claim            23552
perspective      68064
predict_label        1
result               1
Name: 7010, dtype: object 

claim            29184
perspective      29184
predict_label        1
result               1
Name: 7011, dtype: object 

claim            29184
perspective      91170
predict_label        1
result              -1
Name: 7012, dtype: object 

claim            29184
perspective      46658
predict_label        1
result              -1
Name: 7013, dtype: object 

claim            29184
perspective      95616
predict_label        1
result              -1
Name: 7014, dtype: object 

claim            29184
perspective      00033
predict_label        1
result              -1
Name: 7015, dtype: object 

claim            29184
perspective      74305
predict_label       -1
result               1
Name: 7016, dtype: object 

claim       

In [23]:
for i in range((len(newdf3))):
    if newdf3.at[i,'claim'] == newdf3.at[i,'perspective'] and i in unimportantmarks:
        newdf3.at[i,'predict_label'] = 0
        newdf3.at[i,'result'] = 0

In [24]:
#separate reply point system by thread 
elist = []
telist = []
copyforllist = []
llist = []
for i in range(len(newdf3)):
    if newdf3.at[i,'claim'] == newdf3.at[i,'perspective']: #if these numbers are the same, then we have a new thread        
        if i == 0:
            a =(newdf3.at[i,'claim']) #add threadnumber
            telist.append(newdf3.at[i,'result']) #append value to a list
            
        elif i in newsbookmarks:
            aa = tuple((a,telist[:])) #add threadnumber and list with its values to final list
            elist.append(aa)          #add threadnumber and list with its values to final list
            copyforllist.append(aa)
            llist.append(copyforllist[:])
            telist.clear()            #clear temporary list
            copyforllist.clear()
            a =(newdf3.at[i,'claim']) #add threadnumber
            telist.append(newdf3.at[i,'result']) #append value to a list 
            
        else:
            aa = tuple((a,telist[:])) #add threadnumber and list with its values to final list
            elist.append(aa)          #add threadnumber and list with its values to final list
            copyforllist.append(aa)
            telist.clear()            #clear temporary list
            a =(newdf3.at[i,'claim']) #add threadnumber
            telist.append(newdf3.at[i,'result']) #append value to a list
            
    else:
        telist.append(newdf3.at[i,'result']) #append value to a list
aa = tuple((a,telist[:]))
elist.append(aa)
copyforllist.append(aa)
llist.append(copyforllist)
#del elist[0]
#print(len(elist))
#print(elist)

In [25]:
tuplelist = []
for i in range(len(elist)): # [1,-1,-1,-1,1,1,1
    tuple1=tuple((elist[i][0],elist[i][1][0],elist[i][1][1:len(elist)]))
    tuplelist.append(tuple1)

    #divide the tuple into the following:
    #threadnumber, result(if news is true/false), reply-values(1,-1,1.. etc)
    
#for i in range(len(tuplelist)):
#    print(i,tuplelist[i])

In [26]:
counttuple = []
forc = 0
against = 0

df5 =pd.DataFrame(
{"threadnumber" : [],
"news" : [], 
"for" : [], 
"against" : [],
"for%" : [], 
"against%" : [], 
"verdict" : []})

for i in tuplelist:
    #print(i[2])
    for j in range(len(i[2])):
        if (i[2][j] == 1):
            forc += 1
        else:
            against += 1
        #print(i[1][j])
        
    #print(forc,against)
    
    forp = forc/(forc+against)
    againstp = against/(forc+against)
    summed = sum(i[2])
    
    if i[1] > 0 and summed > 0:
        verd = "TP"   #pregnant woman is pregnant
    elif i[1] > 0 and summed < 0:
        verd = "FP"   #pregnant woman is told shes not preg
    elif i[1] < 0 and summed > 0:
        verd = "FN"   #dentist says man is pregnant
    elif i[1] < 0 and summed < 0:
        verd = "TN"   #man is told he is NOT pregnant
    elif i[1] > 0 and summed == 0:
        verd = "UP"   #pregnant woman is by equal amount that she is and is not pregnant
    elif i[1] < 0 and summed == 0:
        verd = "UN"   #man is by equal amount that she is and is not pregnant
    elif i[1] == 0 and summed < 0:
        verd = "TQ"   #true query/comment
    elif i[1] == 0 and summed > 1:
        verd = "FQ"   #false query/comment
    elif i[1] == 0 and summed == 0:
        verd = "UQ"
        
    df5.loc[len(df5.index)] = [i[0], i[1], forc, against, forp, againstp, verd]   
    #print(len(df5))
    forc = 0
    against = 0
df5

threadnumber  news   for  against      for%  against% verdict
0          jvbd8  -1.0   1.0      3.0  0.250000  0.750000      TN
1          1xv6u   1.0   9.0      9.0  0.500000  0.500000      UP
2          dfdvo   0.0   3.0      9.0  0.250000  0.750000      TQ
3          qzxep   0.0   0.0      4.0  0.000000  1.000000      TQ
4          6yxyf   0.0   1.0     14.0  0.066667  0.933333      TQ
..           ...   ...   ...      ...       ...       ...     ...
361        64801   1.0   4.0     15.0  0.210526  0.789474      FP
362        23552   1.0  16.0      0.0  1.000000  0.000000      TP
363        29184   1.0   3.0     13.0  0.187500  0.812500      FP
364        00064   1.0   2.0      0.0  1.000000  0.000000      TP
365        12672   1.0  11.0      7.0  0.611111  0.388889      TP

[366 rows x 7 columns]

In [27]:
reslist = []
df6 = df5.copy()
print(df6)
for i in range(len(llist)):
    print(i, len(llist[i]))
    reslist.append(df6.iloc[0:len(llist[i])])
    df6 = df6.iloc[len(llist[i]):,:]
    print("ln",len(df6))
print(reslist)

    threadnumber  news   for  against      for%  against% verdict
0          jvbd8  -1.0   1.0      3.0  0.250000  0.750000      TN
1          1xv6u   1.0   9.0      9.0  0.500000  0.500000      UP
2          dfdvo   0.0   3.0      9.0  0.250000  0.750000      TQ
3          qzxep   0.0   0.0      4.0  0.000000  1.000000      TQ
4          6yxyf   0.0   1.0     14.0  0.066667  0.933333      TQ
..           ...   ...   ...      ...       ...       ...     ...
361        64801   1.0   4.0     15.0  0.210526  0.789474      FP
362        23552   1.0  16.0      0.0  1.000000  0.000000      TP
363        29184   1.0   3.0     13.0  0.187500  0.812500      FP
364        00064   1.0   2.0      0.0  1.000000  0.000000      TP
365        12672   1.0  11.0      7.0  0.611111  0.388889      TP

[366 rows x 7 columns]
0 10
ln 356
1 30
ln 326
2 326
ln 0
[  threadnumber  news    for  against      for%  against% verdict
0        jvbd8  -1.0    1.0      3.0  0.250000  0.750000      TN
1        1xv6u   1

In [33]:
index = 0

allresulttables = []

for i in reslist:
    resulttable = pd.DataFrame(
    {"thread: true" : [0,0,0],
     "thread: false" : [0,0,0],
     "thread: query/comment" : [0,0,0]}, 
    index = ["opinion: true", "opinion: false", "opinion: undecided"])
    
    TP = (i.verdict == 'TP').sum()
    FP = (i.verdict == 'FP').sum()
    TN = (i.verdict == 'TN').sum()
    FN = (i.verdict == 'FN').sum()
    UP = (i.verdict == 'UP').sum()
    UN = (i.verdict == 'UN').sum()
    TQ = (i.verdict == 'TQ').sum()
    FQ = (i.verdict == 'FQ').sum()
    UQ = (i.verdict == 'UQ').sum()
    
    resulttable.iloc[0][0] = TP
    resulttable.iloc[1][0] = FP
    resulttable.iloc[2][0] = UP
    resulttable.iloc[0][1] = TN
    resulttable.iloc[1][1] = FN
    resulttable.iloc[2][1] = UN
    resulttable.iloc[0][2] = TQ
    resulttable.iloc[1][2] = FQ
    resulttable.iloc[2][2] = UQ    
        
    allresulttables.append(resulttable)
allresulttables   

[                    thread: true  thread: false  thread: query/comment
 opinion: true                  2              1                      4
 opinion: false                 0              0                      2
 opinion: undecided             1              0                      0,
                     thread: true  thread: false  thread: query/comment
 opinion: true                  5              1                     14
 opinion: false                 1              1                      6
 opinion: undecided             0              0                      2,
                     thread: true  thread: false  thread: query/comment
 opinion: true                219              6                      6
 opinion: false                68              5                      3
 opinion: undecided            17              1                      1]

In [34]:
for i in allresulttables:
    display(i)

thread: true  thread: false  thread: query/comment
opinion: true                  2              1                      4
opinion: false                 0              0                      2
opinion: undecided             1              0                      0

thread: true  thread: false  thread: query/comment
opinion: true                  5              1                     14
opinion: false                 1              1                      6
opinion: undecided             0              0                      2

thread: true  thread: false  thread: query/comment
opinion: true                219              6                      6
opinion: false                68              5                      3
opinion: undecided            17              1                      1

In [35]:
index = 0

allpercentresulttables = []

for i in reslist:
    resulttable = pd.DataFrame(
    {"thread: true" : [0,0,0],
     "thread: false" : [0,0,0],
     "thread: query/comment" : [0,0,0]}, 
    index = ["opinion: true", "opinion: false", "opinion: undecided"])
    
    TP = ((i.verdict == 'TP').sum() * 100.)/len(i)
    FP = ((i.verdict == 'FP').sum() * 100.)/len(i)
    TN = ((i.verdict == 'TN').sum() * 100.)/len(i)
    FN = ((i.verdict == 'FN').sum() * 100.)/len(i)
    UP = ((i.verdict == 'UP').sum() * 100.)/len(i)
    UN = ((i.verdict == 'UN').sum() * 100.)/len(i)
    TQ = ((i.verdict == 'TQ').sum() * 100.)/len(i)
    FQ = ((i.verdict == 'FQ').sum() * 100.)/len(i)
    UQ = ((i.verdict == 'UQ').sum() * 100.)/len(i)
    
    resulttable.iloc[0][0] = TP
    resulttable.iloc[1][0] = FP
    resulttable.iloc[2][0] = UP
    resulttable.iloc[0][1] = TN
    resulttable.iloc[1][1] = FN
    resulttable.iloc[2][1] = UN
    resulttable.iloc[0][2] = TQ
    resulttable.iloc[1][2] = FQ
    resulttable.iloc[2][2] = UQ    
        
    allpercentresulttables.append(resulttable)
allpercentresulttables   

[                    thread: true  thread: false  thread: query/comment
 opinion: true                 20             10                     40
 opinion: false                 0              0                     20
 opinion: undecided            10              0                      0,
                     thread: true  thread: false  thread: query/comment
 opinion: true                 16              3                     46
 opinion: false                 3              3                     20
 opinion: undecided             0              0                      6,
                     thread: true  thread: false  thread: query/comment
 opinion: true                 67              1                      1
 opinion: false                20              1                      0
 opinion: undecided             5              0                      0]

In [36]:
for i in allpercentresulttables:
    display(i)

thread: true  thread: false  thread: query/comment
opinion: true                 20             10                     40
opinion: false                 0              0                     20
opinion: undecided            10              0                      0

thread: true  thread: false  thread: query/comment
opinion: true                 16              3                     46
opinion: false                 3              3                     20
opinion: undecided             0              0                      6

thread: true  thread: false  thread: query/comment
opinion: true                 67              1                      1
opinion: false                20              1                      0
opinion: undecided             5              0                      0

In [37]:
index = 0

alltogetherresulttables = []

resulttable = pd.DataFrame(
    {"thread: true" : [0,0,0],
     "thread: false" : [0,0,0],
     "thread: query/comment" : [0,0,0]}, 
    index = ["opinion: true", "opinion: false", "opinion: undecided"])

TP = 0
FP = 0
TN = 0
FN = 0
UP = 0
UN = 0
TQ = 0
FQ = 0
UQ = 0
    
for i in reslist:    
    TP = TP+(i.verdict == 'TP').sum()
    FP = FP+(i.verdict == 'FP').sum()
    TN = TN+(i.verdict == 'TN').sum()
    FN = FN+(i.verdict == 'FN').sum()
    UP = UP+(i.verdict == 'UP').sum()
    UN = UN+(i.verdict == 'UN').sum()
    TQ = TQ+(i.verdict == 'TQ').sum()
    FQ = FQ+(i.verdict == 'FQ').sum()
    UQ = UQ+(i.verdict == 'UQ').sum()
    
    resulttable.iloc[0][0] = TP
    resulttable.iloc[1][0] = FP
    resulttable.iloc[2][0] = UP
    resulttable.iloc[0][1] = TN
    resulttable.iloc[1][1] = FN
    resulttable.iloc[2][1] = UN
    resulttable.iloc[0][2] = TQ
    resulttable.iloc[1][2] = FQ
    resulttable.iloc[2][2] = UQ    
        
alltogetherresulttables.append(resulttable)
display(alltogetherresulttables[0])

thread: true  thread: false  thread: query/comment
opinion: true                226              8                     24
opinion: false                69              6                     11
opinion: undecided            18              1                      3

In [38]:
index = 0

alltogetherpercentresulttables = []

resulttable = pd.DataFrame(
    {"thread: true" : [0,0,0],
     "thread: false" : [0,0,0],
     "thread: query/comment" : [0,0,0]}, 
    index = ["opinion: true", "opinion: false", "opinion: undecided"])

TP = 0
FP = 0
TN = 0
FN = 0
UP = 0
UN = 0
TQ = 0
FQ = 0
UQ = 0
    
for i in reslist:    
    TP = ((i.verdict == 'TP').sum() * 100.)/len(i)
    FP = ((i.verdict == 'FP').sum() * 100.)/len(i)
    TN = ((i.verdict == 'TN').sum() * 100.)/len(i)
    FN = ((i.verdict == 'FN').sum() * 100.)/len(i)
    UP = ((i.verdict == 'UP').sum() * 100.)/len(i)
    UN = ((i.verdict == 'UN').sum() * 100.)/len(i)
    TQ = ((i.verdict == 'TQ').sum() * 100.)/len(i)
    FQ = ((i.verdict == 'FQ').sum() * 100.)/len(i)
    UQ = ((i.verdict == 'UQ').sum() * 100.)/len(i)
    
    resulttable.iloc[0][0] = TP
    resulttable.iloc[1][0] = FP
    resulttable.iloc[2][0] = UP
    resulttable.iloc[0][1] = TN
    resulttable.iloc[1][1] = FN
    resulttable.iloc[2][1] = UN
    resulttable.iloc[0][2] = TQ
    resulttable.iloc[1][2] = FQ
    resulttable.iloc[2][2] = UQ    
        
alltogetherpercentresulttables.append(resulttable)
display(alltogetherpercentresulttables[0])

thread: true  thread: false  thread: query/comment
opinion: true                 67              1                      1
opinion: false                20              1                      0
opinion: undecided             5              0                      0